In [10]:
import pandas as pd
# import rpy2.rinterface 
import numpy as np
from datetime import datetime
# %load_ext rpy2.ipython

In [2]:
# dataframe no qual serão armazenados os resultados
df_fim = pd.DataFrame({'data':[], 'hora':[], 'maquina' :[], 'usuario' : [], 'sessao':[]})
# leitura do arquivo
file = pd.read_csv("../data/logs2.csv", sep=";")
# criação da coluna sesão
file["sessao"] = ""
file.head()

data      hora  maquina              usuario sessao
0  26/01/2016  15:21:01  lcc2-28  2396499187178686315       
1  26/01/2016  15:21:04  lcc2-29  2396499187178686315       
2  26/01/2016  15:30:39  lcc2-26  8842212669098742675       
3  26/01/2016  15:30:55  lcc2-39  2396499187178686315       
4  26/01/2016  15:31:17  lcc2-13  8842212669098742675

In [3]:
# gerando np array sem repetições a partir da coluna usuario
usuarios = file.usuario.unique()
# quantidade de usuarios
file.usuario.unique().size


4065

In [14]:
# iterando por cada um dos usuario que logaram 

for usuario_atual in usuarios:
    # criando um df apenas com os logs do usuario da iteracao
    logs_usuario = file[file["usuario"] == usuario_atual].reset_index()
   
    # formato da hora no df
    formato = "%H:%M:%S"
    # variaveis para auxiliar na verificacao de novas sessoes e tempo de sessao
    dataVez = ""
    horaVez = ""
    maquinaVez = ""
    # armazenar o log intermediario da sesssao
    log_anterior = ""
    # verificando se na iteração anterior a coluna "sessao" foi modificada para "closed"
    previousClosed = False
    
    # iterar sobre cada log do usuario_atual
    for index, logs in logs_usuario.iterrows():
        # verificando se está sendo guardada uma sessao que foi aberta em iteracao anterior ou se está linha do df se refere a uma sessao diferente
        if dataVez == "" and horaVez == "" and maquinaVez == "" or (dataVez != logs["data"] or maquinaVez != logs["maquina"]):
            previousClosed = False
            dataVez = logs["data"]
            horaVez = logs["hora"]
            maquinaVez = logs["maquina"]
            # e o status da linha e na coluna "sessao" deve ser atualizado
            logs_usuario.at[index,"sessao"] = "opened"
            # guardando para fazer comparacao com a proxima sessao
            log_anterior = logs

        # verificando se o log da linha da iteração atual tem a mesma máquina e data e 10 minutos ou menos em relação ao log anterior
        elif (dataVez == logs["data"] and maquinaVez == logs["maquina"] and datetime.strptime(logs.hora,formato) - (datetime.strptime(horaVez,formato))):
            dataVez = logs["data"]
            horaVez = logs["hora"]
            maquinaVez = logs["maquina"]
            # se na linha anterior considerou-se a sessão fechada, essa deve ser considerada como fechamento de sessão e a anterior
            #como de checagem apenas e portanto não deve ter nada na coluna de sessão
            if(previousClosed):
                logs_usuario.at[index-1, "sessao"] = ""
            
            
            logs_usuario.at[index,"sessao"] = "closed"
            previousClosed = True

    # concatenando o data frame dessa iteração com os já processados 
    frames = [df_fim, logs_usuario]
    df_fim = pd.concat(frames)
#     print(logs_usuario)

    index        data      hora  maquina              usuario  sessao
0       0  26/01/2016  15:21:01  lcc2-28  2396499187178686315  opened
1       1  26/01/2016  15:21:04  lcc2-29  2396499187178686315  opened
2       3  26/01/2016  15:30:55  lcc2-39  2396499187178686315  opened
3       5  26/01/2016  15:31:20  lcc2-09  2396499187178686315  opened
4       6  26/01/2016  15:31:23  lcc2-10  2396499187178686315  opened
5       7  26/01/2016  15:31:25  lcc2-11  2396499187178686315  opened
6       9  26/01/2016  15:41:36  lcc2-05  2396499187178686315  opened
7      10  26/01/2016  15:51:30  lcc2-05  2396499187178686315  closed
8      11  26/01/2016  16:00:14  lcc2-21  2396499187178686315  opened
9      12  26/01/2016  16:01:30  lcc2-05  2396499187178686315  opened
10     13  26/01/2016  16:11:30  lcc2-05  2396499187178686315  closed
11     14  26/01/2016  16:11:39  lcc2-02  2396499187178686315  opened
12     15  26/01/2016  16:20:03  lcc2-22  2396499187178686315  opened
13     16  26/01/201

      index        data      hora  maquina              usuario  sessao
0        89  27/01/2016  08:30:25  lcc2-20  -945770275683127821  opened
1        93  27/01/2016  08:40:24  lcc2-20  -945770275683127821        
2        98  27/01/2016  08:50:25  lcc2-20  -945770275683127821        
3       103  27/01/2016  09:00:25  lcc2-20  -945770275683127821  closed
4      7760  15/02/2016  13:50:57  lcc2-17  -945770275683127821  opened
5     10936  17/02/2016  14:01:32  lcc2-06  -945770275683127821  opened
6     11024  17/02/2016  14:31:35  lcc2-04  -945770275683127821  opened
7     20380  29/02/2016  13:41:20  lcc2-10  -945770275683127821  opened
8     20412  29/02/2016  14:01:16  lcc2-13  -945770275683127821  opened
9     20428  29/02/2016  14:11:15  lcc2-13  -945770275683127821        
10    20446  29/02/2016  14:21:15  lcc2-13  -945770275683127821        
11    20465  29/02/2016  14:31:15  lcc2-13  -945770275683127821        
12    20485  29/02/2016  14:41:14  lcc2-13  -945770275683127821 

       index        data      hora  maquina              usuario  sessao
0        105  27/01/2016  09:00:49  lcc2-27  8851394046529841223  opened
1        110  27/01/2016  09:10:49  lcc2-27  8851394046529841223        
2        115  27/01/2016  09:20:48  lcc2-27  8851394046529841223        
3        121  27/01/2016  09:36:13  lcc2-27  8851394046529841223        
4        127  27/01/2016  09:40:48  lcc2-27  8851394046529841223        
5        133  27/01/2016  09:50:50  lcc2-27  8851394046529841223        
6        139  27/01/2016  10:00:49  lcc2-27  8851394046529841223        
7        143  27/01/2016  10:10:49  lcc2-27  8851394046529841223        
8        148  27/01/2016  10:20:49  lcc2-27  8851394046529841223        
9        152  27/01/2016  10:30:49  lcc2-27  8851394046529841223        
10       156  27/01/2016  10:40:50  lcc2-27  8851394046529841223        
11       160  27/01/2016  11:00:49  lcc2-27  8851394046529841223        
12       178  27/01/2016  11:30:48  lcc2-27  885139

      index        data      hora  maquina              usuario  sessao
0       118  27/01/2016  09:21:26  lcc2-12  8914949561969210791  opened
1      4285  03/02/2016  15:51:40  lcc2-05  8914949561969210791  opened
2      4328  03/02/2016  16:31:28  lcc2-06  8914949561969210791  opened
3      4341  03/02/2016  16:41:27  lcc2-06  8914949561969210791        
4      4355  03/02/2016  16:51:40  lcc2-06  8914949561969210791        
5      4372  03/02/2016  17:01:37  lcc2-06  8914949561969210791        
6      4386  03/02/2016  17:11:28  lcc2-06  8914949561969210791        
7      4396  03/02/2016  17:21:28  lcc2-06  8914949561969210791        
8      4405  03/02/2016  17:31:29  lcc2-06  8914949561969210791        
9      4414  03/02/2016  17:41:28  lcc2-06  8914949561969210791  closed
10     7984  15/02/2016  16:11:17  lcc2-09  8914949561969210791  opened
11     8001  15/02/2016  16:21:17  lcc2-09  8914949561969210791        
12     8017  15/02/2016  16:31:17  lcc2-09  8914949561969210791 

      index        data      hora  maquina               usuario  sessao
0       141  27/01/2016  10:01:34  lcc2-04  -1086634677525316721  opened
1       146  27/01/2016  10:11:40  lcc2-02  -1086634677525316721  opened
2       149  27/01/2016  10:21:41  lcc2-02  -1086634677525316721        
3       153  27/01/2016  10:31:39  lcc2-02  -1086634677525316721        
4       158  27/01/2016  10:41:39  lcc2-02  -1086634677525316721        
5       164  27/01/2016  11:01:40  lcc2-02  -1086634677525316721  closed
6       803  27/01/2016  19:30:34  lcc2-32  -1086634677525316721  opened
7       827  27/01/2016  19:40:29  lcc2-32  -1086634677525316721        
8       856  27/01/2016  19:50:30  lcc2-32  -1086634677525316721  closed
9     10858  17/02/2016  13:40:51  lcc2-30  -1086634677525316721  opened
10    10891  17/02/2016  13:50:51  lcc2-30  -1086634677525316721  closed
11    13717  19/02/2016  14:21:08  lcc2-16  -1086634677525316721  opened
12    13745  19/02/2016  14:31:13  lcc2-16  -108663

...

    index        data      hora  maquina  \
0  406435  05/02/2018  14:11:45  lcc2-03   
1  406445  05/02/2018  14:21:45  lcc2-03   
2  406457  05/02/2018  14:31:46  lcc2-03   
3  406469  05/02/2018  14:41:48  lcc2-03   
4  406481  05/02/2018  14:51:45  lcc2-03   
5  406494  05/02/2018  15:01:44  lcc2-03   
6  406507  05/02/2018  15:11:45  lcc2-03   
7  406521  05/02/2018  15:21:44  lcc2-03   
8  406534  05/02/2018  15:31:50  lcc2-03   

                                    usuario  sessao  
0  5387340004605962917,-5946260201032155747  opened  
1  5387340004605962917,-5946260201032155747          
2  5387340004605962917,-5946260201032155747          
3  5387340004605962917,-5946260201032155747          
4  5387340004605962917,-5946260201032155747          
5  5387340004605962917,-5946260201032155747          
6  5387340004605962917,-5946260201032155747          
7  5387340004605962917,-5946260201032155747          
8  5387340004605962917,-5946260201032155747  closed  
    index        da

    index        data      hora  maquina  \
0  407951  06/02/2018  15:21:30  lcc2-11   
1  407972  06/02/2018  15:31:31  lcc2-11   

                                   usuario  sessao  
0  2464335152082666897,7995863693106437687  opened  
1  2464335152082666897,7995863693106437687  closed  
    index        data      hora  maquina  \
0  407977  06/02/2018  15:31:45  lcc2-03   

                                    usuario  sessao  
0  5387340004605962917,-8964805488632447931  opened  
    index        data      hora  maquina  \
0  407987  06/02/2018  15:40:53  lcc2-27   

                                   usuario  sessao  
0  710203151364569887,-8385852833401398067  opened  
    index        data      hora  maquina  \
0  407989  06/02/2018  15:41:07  lcc2-29   

                                     usuario  sessao  
0  -8029875674051901993,-1178106220558975409  opened  
    index        data      hora  maquina  \
0  408247  07/02/2018  08:30:51  lcc2-27   
1  408266  07/02/2018  08:40:

     index        data      hora  maquina  \
0   408797  07/02/2018  12:41:28  lcc2-09   
1   408826  07/02/2018  12:51:27  lcc2-09   
2   408855  07/02/2018  13:01:34  lcc2-09   
3   408887  07/02/2018  13:11:23  lcc2-09   
4   408917  07/02/2018  13:21:23  lcc2-09   
5   408946  07/02/2018  13:31:25  lcc2-09   
6   408978  07/02/2018  13:41:25  lcc2-09   
7   409006  07/02/2018  13:51:24  lcc2-09   
8   409037  07/02/2018  14:01:25  lcc2-09   
9   409070  07/02/2018  14:11:23  lcc2-09   
10  409103  07/02/2018  14:21:23  lcc2-09   
11  409135  07/02/2018  14:31:23  lcc2-09   
12  409167  07/02/2018  14:41:23  lcc2-09   
13  409200  07/02/2018  14:51:23  lcc2-09   
14  409232  07/02/2018  15:01:24  lcc2-09   
15  409263  07/02/2018  15:11:29  lcc2-09   
16  409295  07/02/2018  15:21:24  lcc2-09   
17  409326  07/02/2018  15:31:25  lcc2-09   
18  409351  07/02/2018  15:41:25  lcc2-09   
19  409373  07/02/2018  15:51:35  lcc2-09   
20  409390  07/02/2018  16:01:26  lcc2-09   
21  409408

    index        data      hora  maquina  \
0  409504  07/02/2018  17:20:16  lcc2-21   
1  409521  07/02/2018  17:30:16  lcc2-21   

                                   usuario  sessao  
0  2855422143173463779,4721389562048838079  opened  
1  2855422143173463779,4721389562048838079  closed  
    index        data      hora  maquina  \
0  409513  07/02/2018  17:21:25  lcc2-09   
1  409530  07/02/2018  17:31:24  lcc2-09   

                                    usuario  sessao  
0  -3188480551047257741,8819494289808705231  opened  
1  -3188480551047257741,8819494289808705231  closed  
    index        data      hora  maquina              usuario  sessao
0  409803  08/02/2018  08:31:05  lcc2-28  9201583517783811811  opened
1  409822  08/02/2018  08:41:04  lcc2-28  9201583517783811811        
2  409842  08/02/2018  08:51:04  lcc2-28  9201583517783811811        
3  409863  08/02/2018  09:01:07  lcc2-28  9201583517783811811        
4  409880  08/02/2018  09:11:04  lcc2-28  9201583517783811811  

    index        data      hora  maquina  \
0  410753  08/02/2018  15:10:15  lcc2-21   
1  410778  08/02/2018  15:20:16  lcc2-21   
2  410806  08/02/2018  15:30:16  lcc2-21   
3  410830  08/02/2018  15:40:16  lcc2-21   
4  410849  08/02/2018  15:50:15  lcc2-21   
5  410866  08/02/2018  16:00:15  lcc2-21   
6  410879  08/02/2018  16:10:16  lcc2-21   

                                   usuario  sessao  
0  -2252123563056576803,616329888599911591  opened  
1  -2252123563056576803,616329888599911591          
2  -2252123563056576803,616329888599911591          
3  -2252123563056576803,616329888599911591          
4  -2252123563056576803,616329888599911591          
5  -2252123563056576803,616329888599911591          
6  -2252123563056576803,616329888599911591  closed  
     index        data      hora  maquina  \
0   410781  08/02/2018  15:20:34  lcc2-32   
1   410809  08/02/2018  15:30:36  lcc2-32   
2   410833  08/02/2018  15:40:35  lcc2-32   
3   410852  08/02/2018  15:50:34  lcc2-32  

In [13]:
# removendo as linhas de checagem de sessão aberta e a coluna de index que tinha passado a ser "parte da informação"
df_sessao = df_fim[df_fim['sessao'] != ""].drop('index',axis=1)
df_sessao

data      hora  maquina  sessao  \
0   26/01/2016  15:21:01  lcc2-28  opened   
1   26/01/2016  15:21:04  lcc2-29  opened   
2   26/01/2016  15:30:55  lcc2-39  opened   
3   26/01/2016  15:31:20  lcc2-09  opened   
4   26/01/2016  15:31:23  lcc2-10  opened   
5   26/01/2016  15:31:25  lcc2-11  opened   
6   26/01/2016  15:41:36  lcc2-05  opened   
7   26/01/2016  15:51:30  lcc2-05  closed   
8   26/01/2016  16:00:14  lcc2-21  opened   
9   26/01/2016  16:01:30  lcc2-05  opened   
10  26/01/2016  16:11:30  lcc2-05  closed   
11  26/01/2016  16:11:39  lcc2-02  opened   
12  26/01/2016  16:20:03  lcc2-22  opened   
13  26/01/2016  16:21:30  lcc2-05  opened   
14  26/01/2016  16:30:04  lcc2-22  opened   
15  26/01/2016  16:31:30  lcc2-05  opened   
16  26/01/2016  16:40:04  lcc2-22  opened   
17  26/01/2016  16:41:30  lcc2-05  opened   
18  26/01/2016  16:50:04  lcc2-22  opened   
19  26/01/2016  16:51:30  lcc2-05  opened   
20  26/01/2016  17:00:04  lcc2-22  opened   
21  26/01/2016  17:01:30  lcc2-05  opened   
22  26/01/2016  17:10:04  lcc2-22  opened   
23  26/01/2016  17:11:30  lcc2-05  opened   
24  26/01/2016  17:20:04  lcc2-22  opened   
25  26/01/2016  17:21:31  lcc2-05  opened   
26  26/01/2016  17:30:04  lcc2-22  opened   
27  26/01/2016  17:31:37  lcc2-05  opened   
28  26/01/2016  17:40:04  lcc2-22  opened   
29  26/01/2016  17:41:31  lcc2-05  opened   
..         ...       ...      ...     ...   
19  08/02/2018  15:50:28  lcc2-20  closed   
0   08/02/2018  12:50:42  lcc2-19  opened   
5   08/02/2018  13:40:45  lcc2-19  closed   
0   08/02/2018  13:50:40  lcc2-19  opened   
4   08/02/2018  14:30:40  lcc2-19  closed   
0   08/02/2018  14:40:40  lcc2-19  opened   
7   08/02/2018  15:50:41  lcc2-19  closed   
0   08/02/2018  15:10:15  lcc2-21  opened   
6   08/02/2018  16:10:16  lcc2-21  closed   
0   08/02/2018  15:20:34  lcc2-32  opened   
13  08/02/2018  17:30:34  lcc2-32  closed   
0   08/02/2018  16:30:16  lcc2-21  opened   
0   09/02/2018  11:21:47  lcc2-02  opened   
1   09/02/2018  11:31:47  lcc2-02  closed   
0   09/02/2018  11:31:21  lcc2-13  opened   
7   09/02/2018  12:41:21  lcc2-13  closed   
0   09/02/2018  12:00:32  lcc2-32  opened   
0   09/02/2018  13:31:23  lcc2-13  opened   
2   09/02/2018  13:51:22  lcc2-13  closed   
0   15/02/2018  09:51:15  lcc2-16  opened   
0   15/02/2018  10:11:12  lcc2-16  opened   
10  15/02/2018  11:51:13  lcc2-16  closed   
0   15/02/2018  10:11:47  lcc2-04  opened   
0   15/02/2018  12:00:06  lcc2-23  opened   
10  15/02/2018  13:50:07  lcc2-23  closed   
0   15/02/2018  12:00:26  lcc2-20  opened   
0   15/02/2018  13:21:14  lcc2-16  opened   
2   15/02/2018  14:21:12  lcc2-16  closed   
0   15/02/2018  13:30:27  lcc2-20  opened   
5   15/02/2018  14:20:27  lcc2-20  closed   

                                              usuario  
0                                 2396499187178686315  
1                                 2396499187178686315  
2                                 2396499187178686315  
3                                 2396499187178686315  
4                                 2396499187178686315  
5                                 2396499187178686315  
6                                 2396499187178686315  
7                                 2396499187178686315  
8                                 2396499187178686315  
9                                 2396499187178686315  
10                                2396499187178686315  
11                                2396499187178686315  
12                                2396499187178686315  
13                                2396499187178686315  
14                                2396499187178686315  
15                                2396499187178686315  
16                                2396499187178686315  
17                                2396499187178686315  
18                                2396499187178686315  
19                                2396499187178686315  
20                                239649918

In [15]:
# gravando os data frames no formato de csv
df_fim.to_csv('../data/logs2Sessoes.csv',sep=';')
df_sessao.to_csv('../data/logs2Sessoes2.csv',sep=';')